**Лабораторный практикум по курсу «Распознавание диктора», Университет ИТМО, 2021**

**Лабораторная работа №3. Построение дикторских моделей и их сравнение**

**Цель работы:** изучение процедуры построения дикторских моделей с использованием глубоких нейросетевых архитектур.

**Краткое описание:** в рамках настоящей лабораторной работы предлагается изучить и реализовать схему построения дикторских моделей с использованием глубокой нейросетевой архитектуры, построенной на основе ResNet-блоков. Процедуры обучения и тестирования предлагается рассмотреть по отношению к задаче идентификации на закрытом множестве, то есть для ситуации, когда дикторские классы являются строго заданными. Тестирование полученной системы предполагает использование доли правильных ответов (accuracy) в качестве целевой метрики оценки качества.

**Данные:** в качестве данных для выполнения лабораторной работы предлагается использовать базу [VoxCeleb1](http://www.robots.ox.ac.uk/~vgg/data/voxceleb/vox1.html).

**Содержание лабораторной работы**

1. Подготовка данных для обучения и тестирования блока построения дикторских моделей.

2. Обучение параметров блока построения дикторских моделей без учёта процедуры аугментации данных.

3. Обучение параметров блока построения дикторских моделей с учётом процедуры аугментации данных.

4. Тестированное блока построения дикторских моделей.

In [1]:
# IPython extension to reload modules before executing user code
%load_ext autoreload
%autoreload 2

# Import of modules
import os
import sys

sys.path.append(os.path.realpath('..'))

import torch
import torch.nn as nn
from torch.utils.data import DataLoader

from common import download_dataset, concatenate, extract_dataset, part_extract, download_protocol, split_musan
from exercises_blank import train_dataset_loader, test_dataset_loader, ResNet, MainModel, train_network, test_network
from ResNetBlocks import BasicBlock
from LossFunction import AAMSoftmaxLoss
from Optimizer import SGDOptimizer
from Scheduler import OneCycleLRScheduler
from load_save_pth import saveParameters, loadParameters

ModuleNotFoundError: No module named 'common'

**1. Подготовка данных для обучения и тестирования детектора речевой активности**

В ходе выполнения лабораторной работы необходимы данные для выполнения процедуры обучения и процедуры тестирования нейросетевого блока генерации дикторских моделей. Возьмём в качестве этих данных звукозаписи, сохраненные в формат *wav*, из корпуса [VoxCeleb1 dev set](https://www.robots.ox.ac.uk/~vgg/data/voxceleb/vox1.html). Данный корпус содержит 148,642 звукозаписи (частота дискретизации равна 16кГц) для 1,211 дикторов женского и мужского пола, разговаривающих преимущественно на английском языке.

В рамках настоящего пункта требуется выполнить загрузку и распаковку звуковых wav-файлов из корпуса VoxCeleb1 dev set.

![Рисунок 1](https://analyticsindiamag.com/wp-content/uploads/2020/12/image.png "VoxCeleb. Крупномасштабная аудиовизуальная база данных человеческой речи.")

In [ ]:
# Download VoxCeleb1 (test set)
with open('../data/lists/datasets.txt', 'r') as f:
    lines = f.readlines()

download_dataset(lines, user='voxceleb1902', password='nx0bl2v2', save_path='../data')

Checksum successful vox1_test_wav.zip.
Checksum successful vox1_dev_wav_partaa.
Checksum successful vox1_dev_wav_partab.
Checksum successful vox1_dev_wav_partac.
Checksum successful vox1_dev_wav_partad.


In [ ]:
# Concatenate archives for VoxCeleb1 dev set
with open('../data/lists/concat_arch.txt', 'r') as f:
    lines = f.readlines()

concatenate(lines, save_path='../data')

Checksum successful vox1_dev_wav.zip.


In [ ]:
# Extract VoxCeleb1 dev set
extract_dataset(save_path='../data/voxceleb1_dev', fname='../data/vox1_dev_wav.zip')

Extracting of ../data/vox1_dev_wav.zip is successful.


In [ ]:
# Download VoxCeleb1 identification protocol
with open('../data/lists/protocols.txt', 'r') as f:
    lines = f.readlines()

download_protocol(lines, save_path='../data/voxceleb1_test')

File veri_test2.txt is downloaded.
File iden_split.txt is downloaded.


**2. Обучение параметров блока построения дикторских моделей без учёта процедуры аугментации данных**

Построение современных дикторских моделей, как правило, выполняется с использованием нейросетевых архитектур, многие из которых позаимствованы из области обработки цифровых изображений. Одними из наиболее распространенных нейросетевых архитектур, используемыми для построения дикторских моделей, являются [ResNet-подобные архитектуры](https://arxiv.org/pdf/1512.03385.pdf). В рамках настоящего пункта предлагается выполнить адаптацию нейросетевой архитектуры ResNet34 для решения задачи генерации дикторских моделей (дикторских эмбеддингов). *Дикторский эмбеддинг* – это высокоуровневый вектор-признаков, состоящий, например, из 128, 256 и т.п. значений, содержащий особенности голоса конкретного человека. При решении задачи распознавания диктора можно выделить эталонные и тестовые дикторские эмбеддинги. *Эталонные эмбеддинги* формируются на этапе регистрации дикторской модели определённого человека и находятся в некотором хранилище данных. *Тестовые эмбеддинги* формируются на этапе непосредственного использования системы голосовой биометрии на практике, когда некоторый пользователь пытается получить доступ к соответствующим ресурсам. Система голосовой биометрии сравнивает по определённой метрике эталонные и тестовые эмбеддинги, формируя оценку сравнения, которая, после её обработки блоком принятия решения, позволяет сделать вывод о том, эмбеддинги одинаковых или разных дикторов сравниваются между собой.

Адаптация различных нейросетевых архитектур из обработки изображений к решению задачи построения дикторских моделей является непростой задачей. Возьмём за основу готовое решение, предложенной в рамках [следующей публикации](https://arxiv.org/pdf/2002.06033.pdf) и адаптируем его применительно к выполнению настоящей лабораторной работы.

Необходимо отметить, что построение дикторских моделей, как правило, требует наличия *акустических признаков*, вычисленных для звукозаписей тренировочной, валидационной и тестовой баз данных. В качестве примера подобных признаков в рамках настоящей лабораторной работы воспользуемся *логарифмами энергий на выходе мел-банка фильтров*. Важно отметить, что акустические признаки подвергаются некоторым процедурам предобработки перед их непосредственной передачей в блок построения дикторских моделей. В качестве этих процедур можно выделить: нормализация и масштабирование признаков, сохранение только речевых фреймов на основе разметки детектора речевой активности и т.п.

После того, как акустические признаки подготовлены, они могут быть переданы на блок построения дикторских моделей. Как правило, структура современных дикторских моделей соответствует структуре [x-векторных архитектур](https://www.danielpovey.com/files/2018_icassp_xvectors.pdf). Эти архитектуры состоят из четырёх ключевых элементов:

1. **Фреймовый уровень.** Предназначен для формирования локальных представлений голоса конкретного человека. На этом уровне как раз и применяются нейросетевые архитектуры на базе свёрточных нейронных сетей, например, ResNet, позволяющих с использованием каскадной схемы из множества фильтров с локальной маской захватить некоторый локальный контекст шаблона голоса человека. Выходом фреймового уровня является набор высокоуровневых представлений (карт-признаков), содержащих локальные особенности голоса человека.

2. **Уровень статистического пулинга** позволяет сформировать промежуточный вектор-признаков, фиксированной длины, которая является одинаковой для звукозаписи любой длительности. В ходе работы блока статистического пулинга происходит удаление временной размерности, присутствующей в картах-признаков. Это достигается путём выполнения процедуры усреднения карт-признаков вдоль оси времени. Выходом уровня статистического пулинга являются вектор среднего и вектор среднеквадратического отклонения, вычисленные на основе карт-признаков. Эти вектора конкатенируются и передаются для дальнейшей обработки на сегментом уровне.

3. **Сегментный уровень.** Предназначен для трансформации промежуточного вектора, как правило, высокой размерности, в компактный вектор-признаков, представляющий собой дикторский эмбеддинг. Необходимо отметить, что на сегментном уровне расположены один или несколько полносвязных нейросетевых слоёв, а обработка данных выполняется по отношению ко всей звукозаписи, а не только к некоторому её локальному контексту, как на фреймовом уровне.

4. **Уровень выходного слоя.** Представляет полносвязный слой с softmax-функциями активации. Количество активаций равно числу дикторов в тренирочной выборке. На вход выходноя слоя подаётся дикторский эмбеддинг, а на выходе – формируется набор апостериорных вероятностей, определяющих принадлежность эмбеддинга к одному из дикторских классов в тренировочной выборке. Необходимо отметить, что, как правило, в современных нейросетевых системах построения дикторских моделей выходной используется только на этапе обучения параметров и на этапе тестирования не используется (на этапе тестирования используются только три первых уровня архитектуры).

Обучение модели генерации дикторских эмбеддингов выполняется путём решения задачи *классификации* или, выражаясь терминами из области биометрии, *идентификации на закрытом множестве* (количество дикторских меток является строго фиксированным). В качестве используемой стоимостной функции выступает *категориальная кросс-энтропия*. Обучение выполняется с помощью мини-батчей, содержащих короткие фрагменты карт акустических признаков (длительностью несколько секунд) различных дикторов из тренировочной базы данных. Обучение на коротких фрагментов позволяет избежать сильного переобучения нейросетевой модели. При выполнении процедуры обучения требуется подобрать набор гиперпараметров, выбрать обучения и метод численной оптимизации.

Для успешного выполнения настоящего пункта необходимо сделать следующее:

1. Сгенерировать списки тренировочных, валидационных и тестовых данных на основе идентификационного протокола базы VoxCeleb1, содержащегося в файле **../data/voxceleb1_test/iden_split.txt**. При генерации списков требуется исключить из них звукозаписи дикторов, которые входят в базу [VoxCeleb1 test set](https://thor.robots.ox.ac.uk/~vgg/data/voxceleb/vox1a/vox1_test_wav.zip). Это позволит выполнить тестирования обученных блоков генерации дикторских моделей на протоколе [VoxCeleb1-O cleaned](https://www.robots.ox.ac.uk/~vgg/data/voxceleb/meta/veri_test2.txt), который составлен по отношению к данным из VoxCeleb1 test set, в лабораторной работе №4.

2. Инициализировать обучаемую дикторскую модель, выбрав любой возможный вариант её архитектуры, предлагаемый в рамках лабораторной работы. При реализации блока статистического пулинга предлагается выбрать либо его классический вариант, предложенный в [следующей работе](https://www.danielpovey.com/files/2018_icassp_xvectors.pdf), либо его более продвинутую версию основанную на использовании [механизмов внимания](https://arxiv.org/pdf/1803.10963.pdf). Использование последней версии статистического пулинга позволяет реализовать детектор речевой активности прямо внутри блока построения дикторских моделей.

3. Инициализировать загрузчики тренировочной и валидационной выборки.

4. Инициализировать оптимизатор и планировщик для выполнения процедуры обучения.

5. Описать процедуру валидации/тестирования блока построения дикторских моделей.

6. Описать процедуру обучения и запустить её, контролируя значения стоимостной функции и доли правильных ответов на тренировочном множестве, а также долю правильных ответов на валидационном множестве.

In [ ]:
# Select hyperparameters

# Acoustic features
n_mels            = 40                                   # number of mel filters in bank filters
log_input         = True                                 # logarithm of features by level

# Neural network archtecture
layers            = [3, 4, 6, 3]                         # number of ResNet blocks in different level of frame level
activation        = nn.ReLU                              # activation function used in ResNet blocks
num_filters       = [32, 64, 128, 256]                   # number of filters of ResNet blocks in different level of frame level
encoder_type      = 'SP'                                 # type of statistic pooling layer ('SP'  – classical statistic pooling
                                                         # layer and 'ASP' – attentive statistic pooling)
nOut              = 512                                  # embedding size

# Loss function for angular losses
margin            = 0.35                                 # margin parameter
scale             = 32.0                                 # scale parameter

# Train dataloader
max_frames_train  = 200                                  # number of frame to train
train_path        = '../data/voxceleb1_dev/wav'          # path to train wav files
batch_size_train  = 128                                  # batch size to train
pin_memory        = False                                # pin memory
num_workers_train = 5                                    # number of workers to train
shuffle           = True                                 # shuffling of training examples

# Validation dataloader
max_frames_val    = 1000                                 # number of frame to validate
val_path          = '../data/voxceleb1_dev/wav'          # path to val wav files
batch_size_val    = 128                                  # batch size to validate
num_workers_val   = 5                                    # number of workers to validate

# Test dataloader
max_frames_test   = 1000                                 # number of frame to test
test_path         = '../data/voxceleb1_dev/wav'          # path to val wav files
batch_size_test   = 128                                  # batch size to test
num_workers_test  = 5                                    # number of workers to test

# Optimizer
lr                = 2.5                                  # learning rate value
weight_decay      = 0                                    # weight decay value

# Scheduler
val_interval      = 5                                    # frequency of validation step
max_epoch         = 40                                   # number of epoches

# Augmentation
musan_path        = '../data/musan_split'                # path to splitted SLR17 dataset
rir_path          = '../data/RIRS_NOISES/simulated_rirs' # path to SLR28 dataset

In [ ]:
# Generate data lists
train_list = []
val_list   = []
test_list  = []

with open('../data/voxceleb1_test/iden_split.txt', 'r') as f:
    lines = f.readlines()

black_list = os.listdir('../data/voxceleb1_test/wav')   # exclude speaker IDs from VoxCeleb1 test set
num_train_spk = []                                      # number of train speakers

for line in lines:
    line   = line.strip().split(' ')
    spk_id = line[1].split('/')[0]

    if not (spk_id in black_list):
        num_train_spk.append(spk_id)

    else:
        continue

    # Train list
    if (line[0] == '1'):
        train_list.append(' '.join([spk_id, line[1]]))

    # Validation list
    elif (line[0] == '2'):
        val_list.append(' '.join([spk_id, line[1]]))

    # Test list
    elif (line[0] == '3'):
        test_list.append(' '.join([spk_id, line[1]]))

num_train_spk = len(set(num_train_spk))

In [ ]:
# Initialize model
model      = ResNet(BasicBlock, layers=layers, activation=activation, num_filters=num_filters, nOut=nOut, encoder_type=encoder_type, n_mels=n_mels, log_input=log_input)
trainfunc  = AAMSoftmaxLoss(nOut=nOut, nClasses=num_train_spk, margin=margin, scale=scale)
main_model = MainModel(model, trainfunc).cuda()

Embedding size is 512, encoder SP.
Initialised AAM softmax margin 0.350 scale 32.000.


In [ ]:
# Initialize train dataloader (without augmentation)
train_dataset = train_dataset_loader(train_list=train_list, max_frames=max_frames_train, train_path=train_path)
train_loader  = DataLoader(train_dataset, batch_size=batch_size_train, pin_memory=pin_memory, num_workers=num_workers_train, shuffle=shuffle)

# Initialize validation dataloader
val_dataset = test_dataset_loader(test_list=val_list, max_frames=max_frames_val, test_path=val_path)
val_loader  = DataLoader(val_dataset, batch_size=batch_size_val, num_workers=num_workers_val)

In [ ]:
# Initialize optimizer and scheduler
optimizer = SGDOptimizer(main_model.parameters(), lr=lr, weight_decay=weight_decay)
scheduler = OneCycleLRScheduler(optimizer,
                                pct_start=0.30,
                                cycle_momentum=False,
                                max_lr=lr,
                                div_factor=20,
                                final_div_factor=10000,
                                total_steps=max_epoch*len(train_loader))

Initialised SGD optimizer.
Initialised OneCycle LR scheduler.


In [ ]:
start_epoch = 0
checkpoint_flag = False

if checkpoint_flag:
    start_epoch = loadParameters(main_model, optimizer, scheduler, path='../data/lab3_models/lab3_model_0004.pth')
    start_epoch = start_epoch + 1

# Train model
for num_epoch in range(start_epoch, max_epoch):
    train_loss, train_top1 = train_network(train_loader, main_model, optimizer, scheduler, num_epoch, verbose=True)

    print("Epoch {:1.0f}, Loss (train set) {:f}, Accuracy (train set) {:2.3f}%".format(num_epoch, train_loss, train_top1))

    if (num_epoch + 1)%val_interval == 0:
        _, val_top1 = test_network(val_loader, main_model)

        print("Epoch {:1.0f}, Accuracy (validation set) {:2.3f}%".format(num_epoch, val_top1))

        saveParameters(main_model, optimizer, scheduler, num_epoch, path='../data/lab3_models')

Epoch 0, Batch 1, LR 0.125000 Loss 19.131176, Accuracy 0.000%
Epoch 0, Batch 2, LR 0.125000 Loss 19.193650, Accuracy 0.000%
Epoch 0, Batch 3, LR 0.125000 Loss 19.169873, Accuracy 0.000%
Epoch 0, Batch 4, LR 0.125000 Loss 19.162623, Accuracy 0.000%
Epoch 0, Batch 5, LR 0.125001 Loss 19.136476, Accuracy 0.000%
Epoch 0, Batch 6, LR 0.125001 Loss 19.142705, Accuracy 0.000%
Epoch 0, Batch 7, LR 0.125001 Loss 19.176785, Accuracy 0.000%
Epoch 0, Batch 8, LR 0.125002 Loss 19.246526, Accuracy 0.098%
Epoch 0, Batch 9, LR 0.125002 Loss 19.337107, Accuracy 0.087%
Epoch 0, Batch 10, LR 0.125003 Loss 19.438720, Accuracy 0.234%
Epoch 0, Batch 11, LR 0.125004 Loss 19.597971, Accuracy 0.284%
Epoch 0, Batch 12, LR 0.125004 Loss 19.834626, Accuracy 0.326%
Epoch 0, Batch 13, LR 0.125005 Loss 20.092049, Accuracy 0.300%
Epoch 0, Batch 14, LR 0.125006 Loss 20.194191, Accuracy 0.279%
Epoch 0, Batch 15, LR 0.125007 Loss 20.241022, Accuracy 0.312%
Epoch 0, Batch 16, LR 0.125008 Loss 20.352530, Accuracy 0.293%
E

Epoch 0, Batch 131, LR 0.125627 Loss 19.587403, Accuracy 0.459%
Epoch 0, Batch 132, LR 0.125637 Loss 19.579257, Accuracy 0.456%
Epoch 0, Batch 133, LR 0.125647 Loss 19.570646, Accuracy 0.452%
Epoch 0, Batch 134, LR 0.125657 Loss 19.564676, Accuracy 0.449%
Epoch 0, Batch 135, LR 0.125667 Loss 19.558798, Accuracy 0.446%
Epoch 0, Batch 136, LR 0.125677 Loss 19.554474, Accuracy 0.460%
Epoch 0, Batch 137, LR 0.125687 Loss 19.548453, Accuracy 0.468%
Epoch 0, Batch 138, LR 0.125697 Loss 19.542194, Accuracy 0.476%
Epoch 0, Batch 139, LR 0.125707 Loss 19.537546, Accuracy 0.489%
Epoch 0, Batch 140, LR 0.125717 Loss 19.531221, Accuracy 0.497%
Epoch 0, Batch 141, LR 0.125728 Loss 19.526574, Accuracy 0.510%
Epoch 0, Batch 142, LR 0.125738 Loss 19.519715, Accuracy 0.517%
Epoch 0, Batch 143, LR 0.125749 Loss 19.512078, Accuracy 0.524%
Epoch 0, Batch 144, LR 0.125759 Loss 19.503729, Accuracy 0.543%
Epoch 0, Batch 145, LR 0.125770 Loss 19.495215, Accuracy 0.550%
Epoch 0, Batch 146, LR 0.125781 Loss 19.

Epoch 0, Batch 260, LR 0.127490 Loss 18.850085, Accuracy 1.355%
Epoch 0, Batch 261, LR 0.127509 Loss 18.845384, Accuracy 1.356%
Epoch 0, Batch 262, LR 0.127528 Loss 18.840583, Accuracy 1.360%
Epoch 0, Batch 263, LR 0.127548 Loss 18.836541, Accuracy 1.369%
Epoch 0, Batch 264, LR 0.127567 Loss 18.831162, Accuracy 1.385%
Epoch 0, Batch 265, LR 0.127587 Loss 18.825467, Accuracy 1.397%
Epoch 0, Batch 266, LR 0.127606 Loss 18.820261, Accuracy 1.407%
Epoch 0, Batch 267, LR 0.127626 Loss 18.816799, Accuracy 1.407%
Epoch 0, Batch 268, LR 0.127646 Loss 18.812930, Accuracy 1.411%
Epoch 0, Batch 269, LR 0.127666 Loss 18.807966, Accuracy 1.417%
Epoch 0, Batch 270, LR 0.127686 Loss 18.802550, Accuracy 1.427%
Epoch 0, Batch 271, LR 0.127706 Loss 18.797164, Accuracy 1.433%
Epoch 0, Batch 272, LR 0.127726 Loss 18.791589, Accuracy 1.439%
Epoch 0, Batch 273, LR 0.127746 Loss 18.786519, Accuracy 1.442%
Epoch 0, Batch 274, LR 0.127766 Loss 18.782769, Accuracy 1.446%
Epoch 0, Batch 275, LR 0.127786 Loss 18.

Epoch 0, Batch 389, LR 0.130585 Loss 18.269224, Accuracy 2.770%
Epoch 0, Batch 390, LR 0.130614 Loss 18.264746, Accuracy 2.786%
Epoch 0, Batch 391, LR 0.130643 Loss 18.259889, Accuracy 2.801%
Epoch 0, Batch 392, LR 0.130672 Loss 18.255015, Accuracy 2.828%
Epoch 0, Batch 393, LR 0.130701 Loss 18.250641, Accuracy 2.841%
Epoch 0, Batch 394, LR 0.130730 Loss 18.247409, Accuracy 2.849%
Epoch 0, Batch 395, LR 0.130759 Loss 18.243142, Accuracy 2.860%
Epoch 0, Batch 396, LR 0.130788 Loss 18.239762, Accuracy 2.871%
Epoch 0, Batch 397, LR 0.130818 Loss 18.235791, Accuracy 2.883%
Epoch 0, Batch 398, LR 0.130847 Loss 18.230940, Accuracy 2.897%
Epoch 0, Batch 399, LR 0.130877 Loss 18.226450, Accuracy 2.917%
Epoch 0, Batch 400, LR 0.130906 Loss 18.222759, Accuracy 2.926%
Epoch 0, Batch 401, LR 0.130936 Loss 18.218195, Accuracy 2.948%
Epoch 0, Batch 402, LR 0.130965 Loss 18.214588, Accuracy 2.954%
Epoch 0, Batch 403, LR 0.130995 Loss 18.209787, Accuracy 2.964%
Epoch 0, Batch 404, LR 0.131025 Loss 18.

Epoch 0, Batch 518, LR 0.134910 Loss 17.747410, Accuracy 4.859%
Epoch 0, Batch 519, LR 0.134949 Loss 17.743052, Accuracy 4.886%
Epoch 0, Batch 520, LR 0.134987 Loss 17.740069, Accuracy 4.893%
Epoch 0, Batch 521, LR 0.135026 Loss 17.735480, Accuracy 4.926%
Epoch 0, Batch 522, LR 0.135064 Loss 17.731465, Accuracy 4.945%
Epoch 0, Batch 523, LR 0.135103 Loss 17.727162, Accuracy 4.962%
Epoch 0, Batch 524, LR 0.135141 Loss 17.723608, Accuracy 4.977%
Epoch 0, Batch 525, LR 0.135180 Loss 17.719448, Accuracy 4.997%
Epoch 0, Batch 526, LR 0.135219 Loss 17.715182, Accuracy 5.017%
Epoch 0, Batch 527, LR 0.135258 Loss 17.711115, Accuracy 5.033%
Epoch 0, Batch 528, LR 0.135297 Loss 17.707686, Accuracy 5.040%
Epoch 0, Batch 529, LR 0.135336 Loss 17.703755, Accuracy 5.063%
Epoch 0, Batch 530, LR 0.135375 Loss 17.699950, Accuracy 5.075%
Epoch 0, Batch 531, LR 0.135414 Loss 17.696214, Accuracy 5.101%
Epoch 0, Batch 532, LR 0.135454 Loss 17.691310, Accuracy 5.127%
Epoch 0, Batch 533, LR 0.135493 Loss 17.

...

Epoch 39, Batch 541, LR 0.001850 Loss 0.728749, Accuracy 99.482%
Epoch 39, Batch 542, LR 0.001842 Loss 0.728737, Accuracy 99.483%
Epoch 39, Batch 543, LR 0.001835 Loss 0.729882, Accuracy 99.476%
Epoch 39, Batch 544, LR 0.001828 Loss 0.730223, Accuracy 99.474%
Epoch 39, Batch 545, LR 0.001821 Loss 0.730086, Accuracy 99.475%
Epoch 39, Batch 546, LR 0.001814 Loss 0.729534, Accuracy 99.476%
Epoch 39, Batch 547, LR 0.001806 Loss 0.729343, Accuracy 99.476%
Epoch 39, Batch 548, LR 0.001799 Loss 0.729800, Accuracy 99.477%
Epoch 39, Batch 549, LR 0.001792 Loss 0.730202, Accuracy 99.476%
Epoch 39, Batch 550, LR 0.001785 Loss 0.730149, Accuracy 99.477%
Epoch 39, Batch 551, LR 0.001778 Loss 0.729831, Accuracy 99.478%
Epoch 39, Batch 552, LR 0.001771 Loss 0.729329, Accuracy 99.479%
Epoch 39, Batch 553, LR 0.001764 Loss 0.729317, Accuracy 99.480%
Epoch 39, Batch 554, LR 0.001757 Loss 0.729226, Accuracy 99.480%
Epoch 39, Batch 555, LR 0.001749 Loss 0.729503, Accuracy 99.478%
Epoch 39, Batch 556, LR 0

Epoch 39, Batch 668, LR 0.001043 Loss 0.730149, Accuracy 99.489%
Epoch 39, Batch 669, LR 0.001038 Loss 0.730065, Accuracy 99.490%
Epoch 39, Batch 670, LR 0.001032 Loss 0.729788, Accuracy 99.490%
Epoch 39, Batch 671, LR 0.001027 Loss 0.729889, Accuracy 99.490%
Epoch 39, Batch 672, LR 0.001022 Loss 0.729823, Accuracy 99.490%
Epoch 39, Batch 673, LR 0.001016 Loss 0.730140, Accuracy 99.488%
Epoch 39, Batch 674, LR 0.001011 Loss 0.730327, Accuracy 99.488%
Epoch 39, Batch 675, LR 0.001006 Loss 0.730390, Accuracy 99.487%
Epoch 39, Batch 676, LR 0.001000 Loss 0.730106, Accuracy 99.488%
Epoch 39, Batch 677, LR 0.000995 Loss 0.729987, Accuracy 99.489%
Epoch 39, Batch 678, LR 0.000990 Loss 0.730027, Accuracy 99.487%
Epoch 39, Batch 679, LR 0.000984 Loss 0.730258, Accuracy 99.487%
Epoch 39, Batch 680, LR 0.000979 Loss 0.730173, Accuracy 99.486%
Epoch 39, Batch 681, LR 0.000974 Loss 0.730328, Accuracy 99.486%
Epoch 39, Batch 682, LR 0.000969 Loss 0.729977, Accuracy 99.487%
Epoch 39, Batch 683, LR 0

Epoch 39, Batch 795, LR 0.000468 Loss 0.727739, Accuracy 99.487%
Epoch 39, Batch 796, LR 0.000465 Loss 0.727785, Accuracy 99.488%
Epoch 39, Batch 797, LR 0.000461 Loss 0.727559, Accuracy 99.488%
Epoch 39, Batch 798, LR 0.000457 Loss 0.727882, Accuracy 99.486%
Epoch 39, Batch 799, LR 0.000454 Loss 0.728279, Accuracy 99.484%
Epoch 39, Batch 800, LR 0.000450 Loss 0.728180, Accuracy 99.484%
Epoch 39, Batch 801, LR 0.000447 Loss 0.728271, Accuracy 99.484%
Epoch 39, Batch 802, LR 0.000443 Loss 0.727934, Accuracy 99.485%
Epoch 39, Batch 803, LR 0.000440 Loss 0.727837, Accuracy 99.484%
Epoch 39, Batch 804, LR 0.000436 Loss 0.727480, Accuracy 99.485%
Epoch 39, Batch 805, LR 0.000433 Loss 0.727350, Accuracy 99.484%
Epoch 39, Batch 806, LR 0.000429 Loss 0.727587, Accuracy 99.483%
Epoch 39, Batch 807, LR 0.000426 Loss 0.727667, Accuracy 99.484%
Epoch 39, Batch 808, LR 0.000422 Loss 0.727525, Accuracy 99.484%
Epoch 39, Batch 809, LR 0.000419 Loss 0.727900, Accuracy 99.483%
Epoch 39, Batch 810, LR 0

Epoch 39, Batch 922, LR 0.000125 Loss 0.724129, Accuracy 99.471%
Epoch 39, Batch 923, LR 0.000123 Loss 0.724221, Accuracy 99.472%
Epoch 39, Batch 924, LR 0.000121 Loss 0.723922, Accuracy 99.472%
Epoch 39, Batch 925, LR 0.000119 Loss 0.723961, Accuracy 99.471%
Epoch 39, Batch 926, LR 0.000118 Loss 0.723707, Accuracy 99.472%
Epoch 39, Batch 927, LR 0.000116 Loss 0.723747, Accuracy 99.471%
Epoch 39, Batch 928, LR 0.000114 Loss 0.723616, Accuracy 99.471%
Epoch 39, Batch 929, LR 0.000112 Loss 0.723713, Accuracy 99.471%
Epoch 39, Batch 930, LR 0.000111 Loss 0.723559, Accuracy 99.472%
Epoch 39, Batch 931, LR 0.000109 Loss 0.723464, Accuracy 99.472%
Epoch 39, Batch 932, LR 0.000107 Loss 0.723458, Accuracy 99.473%
Epoch 39, Batch 933, LR 0.000106 Loss 0.723351, Accuracy 99.473%
Epoch 39, Batch 934, LR 0.000104 Loss 0.723550, Accuracy 99.471%
Epoch 39, Batch 935, LR 0.000103 Loss 0.723621, Accuracy 99.471%
Epoch 39, Batch 936, LR 0.000101 Loss 0.723598, Accuracy 99.471%
Epoch 39, Batch 937, LR 0

Epoch 39, Accuracy (validation set) 92.350%


**3. Обучение параметров блока построения дикторских моделей с учётом процедуры аугментации данных**

Известно, что рроцедуры формирования и передачи речевого сигнала могут сопровождаться воздействием шумов и помех, приводящих к искажению сигнала. В качестве примеров искажающих факторов, влияющих на ухудшение качестве речевого сигнала можно привести: импульсный отклик помещения (реверберация), фоновый шум голосов группы нецелевых дикторов, звук телевизора или радиоприёмника и т.п. Разработка конвейера системы голосовой биометрии требует учёта воздействия искажающих факторов на качество её работы. Поскольку процедура построения современных дикторских моделей основана на обучении глубоких нейронных сетей, требующих большие объёмы данных для обучения их параметров, возможным вариантом увеличения тренировочной выборки может являться использование методов аугментации статистических данных. *Аугментация* – методика создания дополнительных обучающих примеров из имеющихся данных путём внесения в них искажений, которые могут потенциально возникнуть на этапе итогового тестирования системы.

Как правило, при решении задачи аугментации данных в речевой обработке используются дополнительные базы шумов и помех. В качестве примеров можно привести базы [SLR17](https://openslr.org/17/) (корпус музыкальных, речевых и шумовых звукозаписей) и [SLR28](https://openslr.org/28/) (база данных реальных и симулированных импульсных откликов комнат, а также изотропных и точечных шумов). Важно отметить, что перед применением с использованием методов аугментации подобных баз к имеющимся данным, требуется убедиться, что частоты дискретизации искажающих баз и оригинальных данных являются одинаковыми. Применительно к рассматриваемому лабораторному практикуму частоты дискретизации всех используемых звукозаписей должны быть равными 16кГц.

Как известно, можно выделить два режима аугментации данных: *онлайн* (применяется в ходе процедуры обучения) и *оффлайн* (применяется до процедуры обучения) аугментацию. В рамках настоящей лабораторной работы предлагается использовать онлайн аугментацию в силу не очень большого набора тренировочных данных и большей гибкости экспериментов, чем вс случае онлайн аугментации. Необходимо отметить, что применение онлайн аугментации на практике замедляет процедуру обучения, по сравнению с оффлайн аугментацией, так как наложение искажений, извлечение акустических признаков и их возможная предобработка требует определённого машинного времени.

В рамках настоящего пункта предлагается сделать следующее:

1. Загрузить и извлечь данные из базы SLR17 (MUSAN). Частота дискретизации данных в рассматриваемой базе равна 16кГц по умолчанию. Поскольку звукозаписи рассматриваемой базы являются достаточно длинными, рекомендуется предварительно разбить эту базу на более маленькие фрагменты (например, длительностью 5 секунд с шагом 3 секунды), сохранив их на диск.

2. Загрузить и извлечь данные из базы SLR28 (MUSAN). Частота дискретизации данных в рассматриваемой базе равна 16кГц по умолчанию.

3. Модернизировать загрузчик тренировочных данных под возможность случайного наложения (искажаем исходные звукозаписи) и не наложения (не искажаем исходные звукозаписи) одного из четырёх типов искажений (реверберация, музыкальный шум, фоновый шум голосов нескольких дикторов, неструктурированный шум), описанных внутри класса **AugmentWAV** следующего программного кода: **../common/DatasetLoader.py**.

4. Используя процедуру обучения из предыдущего пункта с идентичными настройками выполнить тренировку параметров блока генерации дикторских моделей на исходных данных при наличии их аугментирвоанных копий.

In [ ]:
# Download SLR17 (MUSAN) and SLR28 (RIR noises) datasets
with open('../data/lists/augment_datasets.txt', 'r') as f:
    lines = f.readlines()

download_dataset(lines, user=None, password=None, save_path='../data')

Checksum successful musan.tar.gz.
Checksum successful rirs_noises.zip.


In [ ]:
# Extract SLR17 (MUSAN)
extract_dataset(save_path='../data', fname='../data/musan.tar.gz')

# Extract SLR28 (RIR noises)
part_extract(save_path='../data', fname='../data/rirs_noises.zip', target=['RIRS_NOISES/simulated_rirs/mediumroom', 'RIRS_NOISES/simulated_rirs/smallroom'])

Extracting of ../data/musan.tar.gz is successful.
Extracting ../data/rirs_noises.zip


In [ ]:
# Split MUSAN (SLR17) dataset for faster random access
split_musan(save_path='../data')

0 ../data/musan/noise/free-sound/noise-free-sound-0536.wav
1 ../data/musan/noise/free-sound/noise-free-sound-0306.wav
2 ../data/musan/noise/free-sound/noise-free-sound-0115.wav
3 ../data/musan/noise/free-sound/noise-free-sound-0566.wav
4 ../data/musan/noise/free-sound/noise-free-sound-0152.wav
5 ../data/musan/noise/free-sound/noise-free-sound-0527.wav
6 ../data/musan/noise/free-sound/noise-free-sound-0302.wav
7 ../data/musan/noise/free-sound/noise-free-sound-0461.wav
8 ../data/musan/noise/free-sound/noise-free-sound-0141.wav
9 ../data/musan/noise/free-sound/noise-free-sound-0565.wav
10 ../data/musan/noise/free-sound/noise-free-sound-0744.wav
11 ../data/musan/noise/free-sound/noise-free-sound-0336.wav
12 ../data/musan/noise/free-sound/noise-free-sound-0038.wav
13 ../data/musan/noise/free-sound/noise-free-sound-0727.wav
14 ../data/musan/noise/free-sound/noise-free-sound-0445.wav
15 ../data/musan/noise/free-sound/noise-free-sound-0762.wav
16 ../data/musan/noise/free-sound/noise-free-sound

213 ../data/musan/noise/free-sound/noise-free-sound-0430.wav
214 ../data/musan/noise/free-sound/noise-free-sound-0358.wav
215 ../data/musan/noise/free-sound/noise-free-sound-0477.wav
216 ../data/musan/noise/free-sound/noise-free-sound-0563.wav
217 ../data/musan/noise/free-sound/noise-free-sound-0814.wav
218 ../data/musan/noise/free-sound/noise-free-sound-0045.wav
219 ../data/musan/noise/free-sound/noise-free-sound-0616.wav
220 ../data/musan/noise/free-sound/noise-free-sound-0081.wav
221 ../data/musan/noise/free-sound/noise-free-sound-0644.wav
222 ../data/musan/noise/free-sound/noise-free-sound-0200.wav
223 ../data/musan/noise/free-sound/noise-free-sound-0579.wav
224 ../data/musan/noise/free-sound/noise-free-sound-0347.wav
225 ../data/musan/noise/free-sound/noise-free-sound-0685.wav
226 ../data/musan/noise/free-sound/noise-free-sound-0344.wav
227 ../data/musan/noise/free-sound/noise-free-sound-0433.wav
228 ../data/musan/noise/free-sound/noise-free-sound-0203.wav
229 ../data/musan/noise/

392 ../data/musan/noise/free-sound/noise-free-sound-0706.wav
393 ../data/musan/noise/free-sound/noise-free-sound-0554.wav
394 ../data/musan/noise/free-sound/noise-free-sound-0112.wav
395 ../data/musan/noise/free-sound/noise-free-sound-0107.wav
396 ../data/musan/noise/free-sound/noise-free-sound-0101.wav
397 ../data/musan/noise/free-sound/noise-free-sound-0405.wav
398 ../data/musan/noise/free-sound/noise-free-sound-0398.wav
399 ../data/musan/noise/free-sound/noise-free-sound-0834.wav
400 ../data/musan/noise/free-sound/noise-free-sound-0395.wav
401 ../data/musan/noise/free-sound/noise-free-sound-0645.wav
402 ../data/musan/noise/free-sound/noise-free-sound-0491.wav
403 ../data/musan/noise/free-sound/noise-free-sound-0546.wav
404 ../data/musan/noise/free-sound/noise-free-sound-0429.wav
405 ../data/musan/noise/free-sound/noise-free-sound-0289.wav
406 ../data/musan/noise/free-sound/noise-free-sound-0382.wav
407 ../data/musan/noise/free-sound/noise-free-sound-0227.wav
408 ../data/musan/noise/

584 ../data/musan/noise/free-sound/noise-free-sound-0243.wav
585 ../data/musan/noise/free-sound/noise-free-sound-0345.wav
586 ../data/musan/noise/free-sound/noise-free-sound-0501.wav
587 ../data/musan/noise/free-sound/noise-free-sound-0126.wav
588 ../data/musan/noise/free-sound/noise-free-sound-0757.wav
589 ../data/musan/noise/free-sound/noise-free-sound-0239.wav
590 ../data/musan/noise/free-sound/noise-free-sound-0221.wav
591 ../data/musan/noise/free-sound/noise-free-sound-0482.wav
592 ../data/musan/noise/free-sound/noise-free-sound-0652.wav
593 ../data/musan/noise/free-sound/noise-free-sound-0172.wav
594 ../data/musan/noise/free-sound/noise-free-sound-0007.wav
595 ../data/musan/noise/free-sound/noise-free-sound-0274.wav
596 ../data/musan/noise/free-sound/noise-free-sound-0719.wav
597 ../data/musan/noise/free-sound/noise-free-sound-0319.wav
598 ../data/musan/noise/free-sound/noise-free-sound-0812.wav
599 ../data/musan/noise/free-sound/noise-free-sound-0199.wav
600 ../data/musan/noise/

801 ../data/musan/noise/free-sound/noise-free-sound-0105.wav
802 ../data/musan/noise/free-sound/noise-free-sound-0099.wav
803 ../data/musan/noise/free-sound/noise-free-sound-0560.wav
804 ../data/musan/noise/free-sound/noise-free-sound-0595.wav
805 ../data/musan/noise/free-sound/noise-free-sound-0235.wav
806 ../data/musan/noise/free-sound/noise-free-sound-0039.wav
807 ../data/musan/noise/free-sound/noise-free-sound-0637.wav
808 ../data/musan/noise/free-sound/noise-free-sound-0490.wav
809 ../data/musan/noise/free-sound/noise-free-sound-0202.wav
810 ../data/musan/noise/free-sound/noise-free-sound-0449.wav
811 ../data/musan/noise/free-sound/noise-free-sound-0228.wav
812 ../data/musan/noise/free-sound/noise-free-sound-0381.wav
813 ../data/musan/noise/free-sound/noise-free-sound-0024.wav
814 ../data/musan/noise/free-sound/noise-free-sound-0180.wav
815 ../data/musan/noise/free-sound/noise-free-sound-0548.wav
816 ../data/musan/noise/free-sound/noise-free-sound-0095.wav
817 ../data/musan/noise/

...

1411 ../data/musan/music/rfm/music-rfm-0134.wav
1412 ../data/musan/music/rfm/music-rfm-0123.wav
1413 ../data/musan/music/rfm/music-rfm-0098.wav
1414 ../data/musan/music/rfm/music-rfm-0086.wav
1415 ../data/musan/music/rfm/music-rfm-0017.wav
1416 ../data/musan/music/rfm/music-rfm-0082.wav
1417 ../data/musan/music/rfm/music-rfm-0002.wav
1418 ../data/musan/music/rfm/music-rfm-0043.wav
1419 ../data/musan/music/rfm/music-rfm-0042.wav
1420 ../data/musan/music/rfm/music-rfm-0007.wav
1421 ../data/musan/music/rfm/music-rfm-0060.wav
1422 ../data/musan/music/rfm/music-rfm-0091.wav
1423 ../data/musan/music/rfm/music-rfm-0080.wav
1424 ../data/musan/music/rfm/music-rfm-0005.wav
1425 ../data/musan/music/rfm/music-rfm-0045.wav
1426 ../data/musan/music/rfm/music-rfm-0000.wav
1427 ../data/musan/music/rfm/music-rfm-0114.wav
1428 ../data/musan/music/rfm/music-rfm-0136.wav
1429 ../data/musan/music/rfm/music-rfm-0118.wav
1430 ../data/musan/music/rfm/music-rfm-0124.wav
1431 ../data/musan/music/rfm/music-rfm-0

1574 ../data/musan/music/fma-western-art/music-fma-wa-0057.wav
1575 ../data/musan/music/fma-western-art/music-fma-wa-0045.wav
1576 ../data/musan/music/fma-western-art/music-fma-wa-0026.wav
1577 ../data/musan/music/fma-western-art/music-fma-wa-0016.wav
1578 ../data/musan/music/fma-western-art/music-fma-wa-0008.wav
1579 ../data/musan/music/fma-western-art/music-fma-wa-0029.wav
1580 ../data/musan/music/fma-western-art/music-fma-wa-0032.wav
1581 ../data/musan/music/fma-western-art/music-fma-wa-0005.wav
1582 ../data/musan/music/fma-western-art/music-fma-wa-0002.wav
1583 ../data/musan/music/fma-western-art/music-fma-wa-0033.wav
1584 ../data/musan/music/fma-western-art/music-fma-wa-0082.wav
1585 ../data/musan/music/fma-western-art/music-fma-wa-0003.wav
1586 ../data/musan/music/fma-western-art/music-fma-wa-0069.wav
1587 ../data/musan/music/fma-western-art/music-fma-wa-0070.wav
1588 ../data/musan/music/fma-western-art/music-fma-wa-0085.wav
1589 ../data/musan/music/fma-western-art/music-fma-wa-0

1715 ../data/musan/speech/librivox/speech-librivox-0033.wav
1716 ../data/musan/speech/librivox/speech-librivox-0062.wav
1717 ../data/musan/speech/librivox/speech-librivox-0054.wav
1718 ../data/musan/speech/librivox/speech-librivox-0010.wav
1719 ../data/musan/speech/librivox/speech-librivox-0045.wav
1720 ../data/musan/speech/librivox/speech-librivox-0124.wav
1721 ../data/musan/speech/librivox/speech-librivox-0148.wav
1722 ../data/musan/speech/librivox/speech-librivox-0000.wav
1723 ../data/musan/speech/librivox/speech-librivox-0028.wav
1724 ../data/musan/speech/librivox/speech-librivox-0001.wav
1725 ../data/musan/speech/librivox/speech-librivox-0096.wav
1726 ../data/musan/speech/librivox/speech-librivox-0023.wav
1727 ../data/musan/speech/librivox/speech-librivox-0099.wav
1728 ../data/musan/speech/librivox/speech-librivox-0043.wav
1729 ../data/musan/speech/librivox/speech-librivox-0006.wav
1730 ../data/musan/speech/librivox/speech-librivox-0167.wav
1731 ../data/musan/speech/librivox/speec

1860 ../data/musan/speech/us-gov/speech-us-gov-0205.wav
1861 ../data/musan/speech/us-gov/speech-us-gov-0187.wav
1862 ../data/musan/speech/us-gov/speech-us-gov-0249.wav
1863 ../data/musan/speech/us-gov/speech-us-gov-0193.wav
1864 ../data/musan/speech/us-gov/speech-us-gov-0129.wav
1865 ../data/musan/speech/us-gov/speech-us-gov-0055.wav
1866 ../data/musan/speech/us-gov/speech-us-gov-0112.wav
1867 ../data/musan/speech/us-gov/speech-us-gov-0247.wav
1868 ../data/musan/speech/us-gov/speech-us-gov-0242.wav
1869 ../data/musan/speech/us-gov/speech-us-gov-0094.wav
1870 ../data/musan/speech/us-gov/speech-us-gov-0090.wav
1871 ../data/musan/speech/us-gov/speech-us-gov-0211.wav
1872 ../data/musan/speech/us-gov/speech-us-gov-0217.wav
1873 ../data/musan/speech/us-gov/speech-us-gov-0121.wav
1874 ../data/musan/speech/us-gov/speech-us-gov-0125.wav
1875 ../data/musan/speech/us-gov/speech-us-gov-0140.wav
1876 ../data/musan/speech/us-gov/speech-us-gov-0123.wav
1877 ../data/musan/speech/us-gov/speech-us-gov-0

2010 ../data/musan/speech/us-gov/speech-us-gov-0137.wav
2011 ../data/musan/speech/us-gov/speech-us-gov-0114.wav
2012 ../data/musan/speech/us-gov/speech-us-gov-0229.wav
2013 ../data/musan/speech/us-gov/speech-us-gov-0072.wav
2014 ../data/musan/speech/us-gov/speech-us-gov-0023.wav
2015 ../data/musan/speech/us-gov/speech-us-gov-0222.wav


In [ ]:
# Initialize model
model      = ResNet(BasicBlock, layers=layers, activation=activation, num_filters=num_filters, nOut=nOut, encoder_type=encoder_type, n_mels=n_mels, log_input=log_input)
trainfunc  = AAMSoftmaxLoss(nOut=nOut, nClasses=num_train_spk, margin=margin, scale=scale)
main_model = MainModel(model, trainfunc).cuda()

Embedding size is 512, encoder SP.
Initialised AAM softmax margin 0.350 scale 32.000.


In [ ]:
# Initialize train dataloader (without augmentation)
train_dataset = train_dataset_loader(train_list=train_list,
                                     max_frames=max_frames_train,
                                     train_path=train_path,
                                     augment=True,
                                     musan_path=musan_path,
                                     rir_path=rir_path)

train_loader  = DataLoader(train_dataset, batch_size=batch_size_train, pin_memory=pin_memory, num_workers=num_workers_train, shuffle=shuffle)

# Initialize validation dataloader
val_dataset = test_dataset_loader(test_list=val_list, max_frames=max_frames_val, test_path=val_path)
val_loader  = DataLoader(val_dataset, batch_size=batch_size_val, num_workers=num_workers_val)

In [ ]:
# Initialize optimizer and scheduler
optimizer = SGDOptimizer(main_model.parameters(), lr=lr, weight_decay=weight_decay)
scheduler = OneCycleLRScheduler(optimizer,
                                pct_start=0.30,
                                cycle_momentum=False,
                                max_lr=lr,
                                div_factor=20,
                                final_div_factor=10000,
                                total_steps=max_epoch*len(train_loader))

Initialised SGD optimizer.
Initialised OneCycle LR scheduler.


In [ ]:
start_epoch = 0
checkpoint_flag = False

if checkpoint_flag:
    start_epoch = loadParameters(main_model, optimizer, scheduler, path='../data/lab3_models_aug/lab3_model_0004.pth')
    start_epoch = start_epoch + 1

# Train model
for num_epoch in range(start_epoch, max_epoch):
    train_loss, train_top1 = train_network(train_loader, main_model, optimizer, scheduler, num_epoch, verbose=True)

    print("Epoch {:1.0f}, Loss (train set) {:f}, Accuracy (train set) {:2.3f}%".format(num_epoch, train_loss, train_top1))

    if (num_epoch + 1)%val_interval == 0:
        _, val_top1 = test_network(val_loader, main_model)

        print("Epoch {:1.0f}, Accuracy (validation set) {:2.3f}%".format(num_epoch, val_top1))

        saveParameters(main_model, optimizer, scheduler, num_epoch, path='../data/lab3_models_aug')

Epoch 0, Batch 1, LR 0.125000 Loss 19.162251, Accuracy 0.000%
Epoch 0, Batch 2, LR 0.125000 Loss 19.189716, Accuracy 0.000%
Epoch 0, Batch 3, LR 0.125000 Loss 19.150785, Accuracy 0.000%
Epoch 0, Batch 4, LR 0.125000 Loss 19.090136, Accuracy 0.000%
Epoch 0, Batch 5, LR 0.125001 Loss 19.119329, Accuracy 0.000%
Epoch 0, Batch 6, LR 0.125001 Loss 19.138951, Accuracy 0.000%
Epoch 0, Batch 7, LR 0.125001 Loss 19.246316, Accuracy 0.000%
Epoch 0, Batch 8, LR 0.125002 Loss 19.353299, Accuracy 0.000%
Epoch 0, Batch 9, LR 0.125002 Loss 19.423435, Accuracy 0.087%
Epoch 0, Batch 10, LR 0.125003 Loss 19.523954, Accuracy 0.078%
Epoch 0, Batch 11, LR 0.125004 Loss 19.583199, Accuracy 0.071%
Epoch 0, Batch 12, LR 0.125004 Loss 19.633158, Accuracy 0.065%
Epoch 0, Batch 13, LR 0.125005 Loss 19.688372, Accuracy 0.120%
Epoch 0, Batch 14, LR 0.125006 Loss 19.739256, Accuracy 0.112%
Epoch 0, Batch 15, LR 0.125007 Loss 19.795479, Accuracy 0.104%
Epoch 0, Batch 16, LR 0.125008 Loss 19.860456, Accuracy 0.146%
E

Epoch 0, Batch 131, LR 0.125627 Loss 19.569039, Accuracy 0.340%
Epoch 0, Batch 132, LR 0.125637 Loss 19.563909, Accuracy 0.337%
Epoch 0, Batch 133, LR 0.125647 Loss 19.559382, Accuracy 0.341%
Epoch 0, Batch 134, LR 0.125657 Loss 19.555912, Accuracy 0.344%
Epoch 0, Batch 135, LR 0.125667 Loss 19.553814, Accuracy 0.347%
Epoch 0, Batch 136, LR 0.125677 Loss 19.548472, Accuracy 0.350%
Epoch 0, Batch 137, LR 0.125687 Loss 19.545085, Accuracy 0.348%
Epoch 0, Batch 138, LR 0.125697 Loss 19.542120, Accuracy 0.345%
Epoch 0, Batch 139, LR 0.125707 Loss 19.536715, Accuracy 0.348%
Epoch 0, Batch 140, LR 0.125717 Loss 19.531794, Accuracy 0.352%
Epoch 0, Batch 141, LR 0.125728 Loss 19.527042, Accuracy 0.355%
Epoch 0, Batch 142, LR 0.125738 Loss 19.522538, Accuracy 0.363%
Epoch 0, Batch 143, LR 0.125749 Loss 19.518862, Accuracy 0.361%
Epoch 0, Batch 144, LR 0.125759 Loss 19.514336, Accuracy 0.358%
Epoch 0, Batch 145, LR 0.125770 Loss 19.508606, Accuracy 0.366%
Epoch 0, Batch 146, LR 0.125781 Loss 19.

Epoch 0, Batch 260, LR 0.127490 Loss 19.021374, Accuracy 0.688%
Epoch 0, Batch 261, LR 0.127509 Loss 19.016695, Accuracy 0.703%
Epoch 0, Batch 262, LR 0.127528 Loss 19.013439, Accuracy 0.707%
Epoch 0, Batch 263, LR 0.127548 Loss 19.011725, Accuracy 0.707%
Epoch 0, Batch 264, LR 0.127567 Loss 19.008113, Accuracy 0.716%
Epoch 0, Batch 265, LR 0.127587 Loss 19.004645, Accuracy 0.722%
Epoch 0, Batch 266, LR 0.127606 Loss 19.002179, Accuracy 0.725%
Epoch 0, Batch 267, LR 0.127626 Loss 18.998885, Accuracy 0.732%
Epoch 0, Batch 268, LR 0.127646 Loss 18.994972, Accuracy 0.732%
Epoch 0, Batch 269, LR 0.127666 Loss 18.993041, Accuracy 0.735%
Epoch 0, Batch 270, LR 0.127686 Loss 18.989572, Accuracy 0.732%
Epoch 0, Batch 271, LR 0.127706 Loss 18.985690, Accuracy 0.732%
Epoch 0, Batch 272, LR 0.127726 Loss 18.982347, Accuracy 0.732%
Epoch 0, Batch 273, LR 0.127746 Loss 18.978892, Accuracy 0.733%
Epoch 0, Batch 274, LR 0.127766 Loss 18.974348, Accuracy 0.736%
Epoch 0, Batch 275, LR 0.127786 Loss 18.

Epoch 0, Batch 389, LR 0.130585 Loss 18.599216, Accuracy 1.366%
Epoch 0, Batch 390, LR 0.130614 Loss 18.596458, Accuracy 1.376%
Epoch 0, Batch 391, LR 0.130643 Loss 18.592748, Accuracy 1.381%
Epoch 0, Batch 392, LR 0.130672 Loss 18.589935, Accuracy 1.393%
Epoch 0, Batch 393, LR 0.130701 Loss 18.587615, Accuracy 1.396%
Epoch 0, Batch 394, LR 0.130730 Loss 18.583714, Accuracy 1.402%
Epoch 0, Batch 395, LR 0.130759 Loss 18.581205, Accuracy 1.406%
Epoch 0, Batch 396, LR 0.130788 Loss 18.577311, Accuracy 1.417%
Epoch 0, Batch 397, LR 0.130818 Loss 18.573936, Accuracy 1.421%
Epoch 0, Batch 398, LR 0.130847 Loss 18.571376, Accuracy 1.427%
Epoch 0, Batch 399, LR 0.130877 Loss 18.568638, Accuracy 1.429%
Epoch 0, Batch 400, LR 0.130906 Loss 18.566025, Accuracy 1.430%
Epoch 0, Batch 401, LR 0.130936 Loss 18.562686, Accuracy 1.442%
Epoch 0, Batch 402, LR 0.130965 Loss 18.559901, Accuracy 1.442%
Epoch 0, Batch 403, LR 0.130995 Loss 18.555872, Accuracy 1.450%
Epoch 0, Batch 404, LR 0.131025 Loss 18.

Epoch 0, Batch 518, LR 0.134910 Loss 18.206179, Accuracy 2.440%
Epoch 0, Batch 519, LR 0.134949 Loss 18.202378, Accuracy 2.454%
Epoch 0, Batch 520, LR 0.134987 Loss 18.198164, Accuracy 2.470%
Epoch 0, Batch 521, LR 0.135026 Loss 18.195509, Accuracy 2.489%
Epoch 0, Batch 522, LR 0.135064 Loss 18.192718, Accuracy 2.499%
Epoch 0, Batch 523, LR 0.135103 Loss 18.189293, Accuracy 2.519%
Epoch 0, Batch 524, LR 0.135141 Loss 18.186021, Accuracy 2.527%
Epoch 0, Batch 525, LR 0.135180 Loss 18.183362, Accuracy 2.537%
Epoch 0, Batch 526, LR 0.135219 Loss 18.180855, Accuracy 2.543%
Epoch 0, Batch 527, LR 0.135258 Loss 18.177535, Accuracy 2.553%
Epoch 0, Batch 528, LR 0.135297 Loss 18.174594, Accuracy 2.558%
Epoch 0, Batch 529, LR 0.135336 Loss 18.171176, Accuracy 2.574%
Epoch 0, Batch 530, LR 0.135375 Loss 18.168558, Accuracy 2.581%
Epoch 0, Batch 531, LR 0.135414 Loss 18.165383, Accuracy 2.591%
Epoch 0, Batch 532, LR 0.135454 Loss 18.162776, Accuracy 2.599%
Epoch 0, Batch 533, LR 0.135493 Loss 18.

...

Epoch 39, Batch 512, LR 0.002066 Loss 3.485889, Accuracy 93.250%
Epoch 39, Batch 513, LR 0.002059 Loss 3.485375, Accuracy 93.254%
Epoch 39, Batch 514, LR 0.002051 Loss 3.484422, Accuracy 93.258%
Epoch 39, Batch 515, LR 0.002043 Loss 3.483252, Accuracy 93.263%
Epoch 39, Batch 516, LR 0.002036 Loss 3.485554, Accuracy 93.253%
Epoch 39, Batch 517, LR 0.002028 Loss 3.486145, Accuracy 93.253%
Epoch 39, Batch 518, LR 0.002020 Loss 3.484533, Accuracy 93.258%
Epoch 39, Batch 519, LR 0.002013 Loss 3.483436, Accuracy 93.262%
Epoch 39, Batch 520, LR 0.002005 Loss 3.483801, Accuracy 93.263%
Epoch 39, Batch 521, LR 0.001998 Loss 3.484275, Accuracy 93.261%
Epoch 39, Batch 522, LR 0.001990 Loss 3.483397, Accuracy 93.261%
Epoch 39, Batch 523, LR 0.001983 Loss 3.483128, Accuracy 93.259%
Epoch 39, Batch 524, LR 0.001975 Loss 3.484258, Accuracy 93.258%
Epoch 39, Batch 525, LR 0.001968 Loss 3.484934, Accuracy 93.253%
Epoch 39, Batch 526, LR 0.001960 Loss 3.484670, Accuracy 93.254%
Epoch 39, Batch 527, LR 0

Epoch 39, Batch 639, LR 0.001207 Loss 3.484197, Accuracy 93.259%
Epoch 39, Batch 640, LR 0.001201 Loss 3.484368, Accuracy 93.257%
Epoch 39, Batch 641, LR 0.001195 Loss 3.484394, Accuracy 93.259%
Epoch 39, Batch 642, LR 0.001190 Loss 3.484655, Accuracy 93.261%
Epoch 39, Batch 643, LR 0.001184 Loss 3.484938, Accuracy 93.255%
Epoch 39, Batch 644, LR 0.001178 Loss 3.486040, Accuracy 93.251%
Epoch 39, Batch 645, LR 0.001172 Loss 3.486974, Accuracy 93.250%
Epoch 39, Batch 646, LR 0.001166 Loss 3.487304, Accuracy 93.252%
Epoch 39, Batch 647, LR 0.001161 Loss 3.487887, Accuracy 93.243%
Epoch 39, Batch 648, LR 0.001155 Loss 3.487557, Accuracy 93.246%
Epoch 39, Batch 649, LR 0.001149 Loss 3.487270, Accuracy 93.247%
Epoch 39, Batch 650, LR 0.001144 Loss 3.487035, Accuracy 93.250%
Epoch 39, Batch 651, LR 0.001138 Loss 3.486590, Accuracy 93.248%
Epoch 39, Batch 652, LR 0.001132 Loss 3.486774, Accuracy 93.249%
Epoch 39, Batch 653, LR 0.001127 Loss 3.486259, Accuracy 93.250%
Epoch 39, Batch 654, LR 0

Epoch 39, Batch 766, LR 0.000579 Loss 3.484496, Accuracy 93.223%
Epoch 39, Batch 767, LR 0.000575 Loss 3.484564, Accuracy 93.221%
Epoch 39, Batch 768, LR 0.000571 Loss 3.484191, Accuracy 93.223%
Epoch 39, Batch 769, LR 0.000567 Loss 3.484475, Accuracy 93.221%
Epoch 39, Batch 770, LR 0.000563 Loss 3.483685, Accuracy 93.224%
Epoch 39, Batch 771, LR 0.000559 Loss 3.483191, Accuracy 93.225%
Epoch 39, Batch 772, LR 0.000555 Loss 3.484055, Accuracy 93.223%
Epoch 39, Batch 773, LR 0.000551 Loss 3.484082, Accuracy 93.224%
Epoch 39, Batch 774, LR 0.000547 Loss 3.483663, Accuracy 93.225%
Epoch 39, Batch 775, LR 0.000543 Loss 3.482991, Accuracy 93.228%
Epoch 39, Batch 776, LR 0.000540 Loss 3.483530, Accuracy 93.221%
Epoch 39, Batch 777, LR 0.000536 Loss 3.484323, Accuracy 93.215%
Epoch 39, Batch 778, LR 0.000532 Loss 3.484347, Accuracy 93.216%
Epoch 39, Batch 779, LR 0.000528 Loss 3.485362, Accuracy 93.215%
Epoch 39, Batch 780, LR 0.000524 Loss 3.485229, Accuracy 93.216%
Epoch 39, Batch 781, LR 0

Epoch 39, Batch 893, LR 0.000183 Loss 3.484948, Accuracy 93.243%
Epoch 39, Batch 894, LR 0.000181 Loss 3.485626, Accuracy 93.241%
Epoch 39, Batch 895, LR 0.000178 Loss 3.485830, Accuracy 93.236%
Epoch 39, Batch 896, LR 0.000176 Loss 3.485523, Accuracy 93.237%
Epoch 39, Batch 897, LR 0.000174 Loss 3.485455, Accuracy 93.238%
Epoch 39, Batch 898, LR 0.000172 Loss 3.485839, Accuracy 93.234%
Epoch 39, Batch 899, LR 0.000170 Loss 3.486088, Accuracy 93.233%
Epoch 39, Batch 900, LR 0.000168 Loss 3.486542, Accuracy 93.232%
Epoch 39, Batch 901, LR 0.000165 Loss 3.486507, Accuracy 93.230%
Epoch 39, Batch 902, LR 0.000163 Loss 3.485734, Accuracy 93.232%
Epoch 39, Batch 903, LR 0.000161 Loss 3.485688, Accuracy 93.231%
Epoch 39, Batch 904, LR 0.000159 Loss 3.486073, Accuracy 93.230%
Epoch 39, Batch 905, LR 0.000157 Loss 3.487370, Accuracy 93.217%
Epoch 39, Batch 906, LR 0.000155 Loss 3.486277, Accuracy 93.219%
Epoch 39, Batch 907, LR 0.000153 Loss 3.486251, Accuracy 93.222%
Epoch 39, Batch 908, LR 0

Epoch 39, Batch 1019, LR 0.000018 Loss 3.478254, Accuracy 93.278%
Epoch 39, Batch 1020, LR 0.000018 Loss 3.478123, Accuracy 93.280%
Epoch 39, Batch 1021, LR 0.000017 Loss 3.478062, Accuracy 93.278%
Epoch 39, Batch 1022, LR 0.000017 Loss 3.477604, Accuracy 93.278%
Epoch 39, Batch 1023, LR 0.000017 Loss 3.477715, Accuracy 93.279%
Epoch 39, Batch 1024, LR 0.000016 Loss 3.478340, Accuracy 93.276%
Epoch 39, Batch 1025, LR 0.000016 Loss 3.478309, Accuracy 93.277%
Epoch 39, Batch 1026, LR 0.000016 Loss 3.478136, Accuracy 93.278%
Epoch 39, Batch 1027, LR 0.000015 Loss 3.478422, Accuracy 93.279%
Epoch 39, Batch 1028, LR 0.000015 Loss 3.478411, Accuracy 93.276%
Epoch 39, Batch 1029, LR 0.000015 Loss 3.478405, Accuracy 93.275%
Epoch 39, Batch 1030, LR 0.000015 Loss 3.478196, Accuracy 93.277%
Epoch 39, Batch 1031, LR 0.000014 Loss 3.477877, Accuracy 93.277%
Epoch 39, Batch 1032, LR 0.000014 Loss 3.477039, Accuracy 93.281%
Epoch 39, Batch 1033, LR 0.000014 Loss 3.476900, Accuracy 93.283%
Epoch 39, 

**4. Тестирование блока построения дикторских моделей**

Из литературы известно, что применение алгоритмов машинного обучения на практике требует использования трёх наборов данных: *тренировочное множество* (используется для обучения параметров модели), *валидационное множество* (используется для настройки гиперпараметров), *тестовое множество* (используется для итогового тестирования).

В рамках настоящего пункта предлагается выполнить итоговое тестирования блоков генерации дикторских моделей, обученных без аугментации и с аугментацией тренировочных данных, и сравнить полученные результаты. При проведении процедуры тестирования рекомендуется выбрать различное количество фреймов для тестовых звукозаписей, чтобы грубо понять то, как длительность фонограммы влияет на качество распознавания диктора.

В качестве целевой метрики предлагается использовать *долю правильных ответов*, то есть количество верно классифицированных объектов по отношению к общему количеству объектов тестового множества. Как и при проведении процедуры обучения и валидации, рассматриваемая процедура тестирования предполагает решение задачи идентификации диктора на закрытом множестве.

In [ ]:
# Initialize test dataloader
test_dataset = test_dataset_loader(test_list=test_list, max_frames=max_frames_test, test_path=test_path)
test_loader = DataLoader(test_dataset, batch_size=batch_size_test, num_workers=num_workers_test)

In [ ]:
# Load model without augmentation
num_epoch = loadParameters(main_model, optimizer, scheduler, path='../data/lab3_models/lab3_model_0039.pth')

# Test model
_, test_top1 = test_network(test_loader, main_model)

print("Epoch {:1.0f}, Accuracy (test set) {:2.3f}%".format(num_epoch, test_top1))

Epoch 39, Accuracy (test set) 92.732%


In [ ]:
# Load model with augmentation
num_epoch = loadParameters(main_model, optimizer, scheduler, path='../data/lab3_models_aug/lab3_model_0039.pth')

# Test model
_, test_top1 = test_network(test_loader, main_model)

print("Epoch {:1.0f}, Accuracy (test set) {:2.3f}%".format(num_epoch, test_top1))

Epoch 39, Accuracy (test set) 92.099%


**5. Контрольные вопросы**

1. Что такое верификация и идентицикация диктора?

2. Что такое распознавание диктора на закрытом и открытом множестве?

3. Что такое текстозависимое и текстонезависимое распознавание диктора?

4. Описать схему обучения блока генерации дикторских моделей на основе нейронных сетей.

5. Описать основные компоненты, из которых состоит нейросетевой блок генерации дикторских моделей (фреймовый уровень, слой статистического пулинга, сегментный уровень, выходной слой).

6. Как устроены нейросетевые архитектуры на основе ResNet-блоков?

7. Что такое полносвязная нейронная сеть прямого распространения?

8. Как устроена стоимостная функция для обучения нейросетевого блока генерации дикторских моделей?

9. Что такое аугментация данных?

10. Что такое дикторский эмбеддинг и на каком уровне блока построения дикторских моделей он генерируется?

**6. Список литературы**

1. Bai Z., Zhang X.-L., Chen J. Speaker recognition based on deep learning: an overview // 	arXiv:2012.00931 [eess.AS] ([ссылка](https://arxiv.org/pdf/2012.00931.pdf)).

2. Hansen J.H.L., Hasan T. Speaker recognition by machines and humans: a tutorial review // IEEE Signal Processing Magazine, 2015. V. 32. № 6. P. 74–99 ([ссылка](https://www.researchgate.net/publication/282940395_Speaker_Recognition_by_Machines_and_Humans_A_tutorial_review)).